In [35]:
import json
import datetime
from splitwise import Splitwise
from ynab_sdk import YNAB
from ynab_sdk.api.models.requests.transaction import TransactionRequest

In [36]:
# Open JSON files

config_path = "config.json"
transactions_path = "data/transactions.json"

with open(config_path, 'r') as j:
    config = json.loads(j.read())
with open(transactions_path, 'r') as j:
    transactions = json.loads(j.read())

In [37]:
# Get Splitwise transaction IDs

transaction_sw_ids = []

for x in transactions:
    transaction_sw_ids.append(x['splitwise_id'])

In [38]:
# Read config

ynab_key = config['ynab']['api_key']
ynab_budget = config['ynab']['budget_name']
ynab_account = config['ynab']['account_name']
sw_consumer_key = config['splitwise']['consumer_key']
sw_consumer_secret = config['splitwise']['consumer_secret']
sw_api_key = config['splitwise']['api_key']
sw_friend_name = config['splitwise']['friend_name']
sw_user_name = config['splitwise']['user_name']
days_included = config['general']['days_included']

In [39]:
# Setup Splitwise and YNAB APIs

sw = Splitwise(sw_consumer_key, sw_consumer_secret, api_key=sw_api_key)
ynab = YNAB(ynab_key)

In [40]:
# Get Splitwise user info

sw_user = sw.getCurrentUser()
sw_user_id = sw_user.getId()

In [41]:
# Get Budget ID and Account ID of YNAB

ynab_budgets = ynab.budgets.get_budgets().data.budgets
ynab_budget_ids = {}
for i, x in enumerate(ynab_budgets):
    ynab_budget_ids[ynab_budgets[i].name] = ynab_budgets[i].id

ynab_budget_id = ynab_budget_ids[ynab_budget]

ynab_accounts = ynab.accounts.get_accounts(budget_id=ynab_budget_id).data.accounts
ynab_account_ids = {}
for i, x in enumerate(ynab_accounts):
    ynab_account_ids[ynab_accounts[i].name] = ynab_accounts[i].id

ynab_account_id = ynab_account_ids[ynab_account]

In [42]:
# Get YNAB Payees and Categories

ynab_payees = ynab.payees.get_payees(budget_id=ynab_budget_id).data.payees
ynab_payee_ids = {}
for i, x in enumerate(ynab_payees):
    ynab_payee_ids[ynab_payees[i].name] = ynab_payees[i].id

ynab_category_groups = ynab.categories.get_categories(budget_id=ynab_budget_id).data.category_groups
ynab_categories = []
for x in ynab_category_groups:
    ynab_categories.extend(x.categories)
ynab_category_ids = {}
for i, x in enumerate(ynab_categories):
    ynab_category_ids[ynab_categories[i].name] = ynab_categories[i].id

In [43]:
# Get ID of Splitwise friend and Friend object

sw_friend_ids = {}
sw_friends = sw.getFriends()
for i, x in enumerate(sw_friends):
    first_name = sw_friends[i].getFirstName()
    last_name = sw_friends[i].getLastName()
    id = sw_friends[i].getId()
    sw_friend_ids[f"{first_name} {last_name}"] = id

sw_friend_id = sw_friend_ids[sw_friend_name]
sw_friend = sw.getUser(sw_friend_id)

In [44]:
def splitwise_id_to_name(debtor_id, creditor_id):
    if (debtor_id == sw_user_id) and (creditor_id == sw_friend_ids[sw_friend_name]):
        debtor = sw_user_name
        creditor = sw_friend_name
    elif (debtor_id == sw_friend_ids[sw_friend_name]) and (creditor_id == sw_user_id):
        debtor = sw_friend_name
        creditor = sw_user_name
    else:
        debtor = "error"
        creditor = "error"
    return debtor, creditor

In [45]:
date_today = datetime.datetime.now()
datetime_after = date_today - datetime.timedelta(days=days_included)
date_after = datetime_after.isoformat()

In [46]:
sw_new_expenses = [exp for exp in sw.getExpenses(limit=0, dated_after=date_after) if exp.repayments[0].getToUser() == sw_friend_ids[sw_friend_name]]

In [47]:
sw_expense_data = []
for exp in sw_new_expenses:
    exp_amount = exp.getCost()
    exp_description = exp.getDescription()
    exp_date = exp.getDate()[:10]  
    exp_id = exp.getId()
    exp_creditor_id = exp.getRepayments()[0].getToUser()
    exp_debtor_id = exp.getRepayments()[0].getFromUser()
    exp_debt = "-" + exp.getRepayments()[0].getAmount()
    exp_credit = str(round(float(exp_amount) + float(exp_debt),2))
    exp_deleted = 'true' if exp.getDeletedBy() else 'false'

    exp_debtor, exp_creditor = splitwise_id_to_name(debtor_id=exp_debtor_id, creditor_id=exp_creditor_id)

    exp_dict = {}

    exp_dict["origin"] = "Splitwise"
    exp_dict["description"] = exp_description
    exp_dict["amount"] = exp_amount
    exp_dict["date"] = exp_date
    exp_dict["creditor"] = exp_creditor
    exp_dict["creditor_id"] = exp_creditor_id
    exp_dict["debtor"] = exp_debtor
    exp_dict["debtor_id"] = exp_debtor_id
    exp_dict["debt"] = exp_debt
    exp_dict["credit"] = exp_credit
    exp_dict["deleted"] = exp_deleted
    exp_dict["splitwise_id"] = exp_id
    sw_expense_data.append(exp_dict)

In [48]:
ynab_new_transactions = []
ynab_new_transaction_sw_ids = []
ynab_transactions_to_delete = transaction_sw_ids.copy()
sw_new_expense_data = sw_expense_data.copy()
sw_update_expense_data = []

In [49]:
for x in sw_expense_data:
    ynab_transaction_sw_id = x['splitwise_id']
    # if expense on SW already exists in transaction file
    if ynab_transaction_sw_id in ynab_transactions_to_delete:
        # remove transaction from transactions to be deleted and continue to next
        ynab_transactions_to_delete.remove(ynab_transaction_sw_id)
        # remove expense from the expense data, the final list will be used to copy to transactions
        sw_new_expense_data.remove(x)
        # add to potential update list
        sw_update_expense_data.append(x)
        continue

    if x['deleted'] == 'true':
            ynab_transaction_amount = 0
            ynab_transaction_memo = f"REMOVED FROM SPLITWISE - {x['description']}"
    elif x['deleted'] == 'false':
            ynab_transaction_amount = int(float(x['debt']) * 1000)
            ynab_transaction_memo = x['description']
    
    ynab_transaction_date = x['date']
    ynab_transaction_payee_name = x['creditor']
    ynab_transaction_payee_id = ynab_payee_ids[ynab_transaction_payee_name]
    ynab_new_transaction = TransactionRequest(account_id=ynab_account_id, date=ynab_transaction_date, amount=ynab_transaction_amount, payee_name=ynab_transaction_payee_name, payee_id=ynab_transaction_payee_id, memo=ynab_transaction_memo)
    ynab_new_transactions.append(ynab_new_transaction)
    ynab_new_transaction_sw_ids.append(x['splitwise_id'])

In [50]:
# Determine which transactions should be updated

remove_from_update_list = []
for i, x in enumerate(sw_update_expense_data):
    remove_from_update = True
    for y in transactions:
        if x['splitwise_id'] == y['splitwise_id']:
            sw_update_expense_data[i]['ynab_id'] = y['ynab_id']
            for z in list(x.keys()):
                if x[z] != y[z]:
                    remove_from_update = False
    if remove_from_update:
        remove_from_update_list.append(x)
for x in remove_from_update_list:
    sw_update_expense_data.remove(x)

In [51]:
def check_valid_date(str_date):
    date_to_check = datetime.datetime.strptime(str_date, '%Y-%m-%d')
    difference = (date_to_check - datetime_after).days
    if difference >= -1:
        return True
    else:
        return False

In [52]:
# Get transactions from YNAB to see the category IDs for the updated transactions

transactions_from_ynab = ynab.transactions.get_transactions_from_account(budget_id=ynab_budget_id, account_id=ynab_account_id).data.transactions

transactions_from_ynab = [x for x in transactions_from_ynab if (check_valid_date(x.date)) and (x.payee_name==sw_friend_name)]
category_ids_from_ynab_transactions = {}

for x in transactions_from_ynab:
    category_ids_from_ynab_transactions[x.id] = ynab_category_ids[x.category_name]

In [53]:
# Update the transactions on YNAB that need to be updated or deleted

if sw_update_expense_data:
    for x in sw_update_expense_data:        

        ynab_transaction_date = x['date']
        
        ynab_transaction_payee_name = x['creditor']
        ynab_transaction_payee_id = ynab_payee_ids[ynab_transaction_payee_name]
        
        ynab_transaction_id = x['ynab_id']
        ynab_transaction_category_id = category_ids_from_ynab_transactions[ynab_transaction_id]

        if x['deleted'] == 'false':
            ynab_transaction_amount = int(float(x['debt']) * 1000)
            ynab_transaction_memo = x['description']
        elif x['deleted'] == 'true':
            ynab_transaction_amount = 0
            ynab_transaction_memo = f"REMOVED FROM SPLITWISE - {x['description']}"

        ynab_updated_transaction = TransactionRequest(account_id=ynab_account_id, date=ynab_transaction_date, amount=ynab_transaction_amount, payee_name=ynab_transaction_payee_name, payee_id=ynab_transaction_payee_id, memo=ynab_transaction_memo, category_id=ynab_transaction_category_id)

        ynab.transactions.update_transaction(budget_id=ynab_budget_id, transaction_id=ynab_transaction_id, transaction=ynab_updated_transaction)
        print(f"{ynab_transaction_memo} updated")

In [54]:
# Create new transactions in YNAB and save new JSON transactions file

if ynab_new_transactions:
    creation_output = ynab.transactions.create_transactions(budget_id=ynab_budget_id, transactions=ynab_new_transactions)

    ynab_new_transactions_ynab = creation_output['data']['transactions']
    ynab_new_transaction_ynab_ids = [d['id'] for d in creation_output['data']['transactions']]

    print("creation_output", creation_output)
    print("ynab_new_transactions_ynab", ynab_new_transactions_ynab)

    # new_transaction_dict = {}

    # for i, x in enumerate(ynab_new_transaction_sw_ids):
    #     new_transaction_dict[ynab_new_transaction_sw_ids[i]] = ynab_new_transaction_ynab_ids[-1 - i]

    # for x in sw_new_expense_data:
    #     x['ynab_id'] = new_transaction_dict[x['splitwise_id']]


# sw_new_expense_data.extend(sw_update_expense_data)
# sw_new_expense_data.extend(remove_from_update_list)

# with open(transactions_path, "w") as outfile:
#     json.dump(sw_new_expense_data, outfile, indent=2)


creation_output {'data': {'transaction_ids': ['9a75f64e-39ab-453d-bd1f-950329449cb3', 'c56a0322-4527-4eab-8b41-4ab9e3fec2af', '74bb1859-1c24-4495-b8e4-2de9bafd27fb', '584232cd-24ef-44e3-ae0a-dfdc99bc36f0', '41447d4c-8fc5-4533-9ab1-aa78fdb05eca', '62a5438d-9b26-41a6-822d-09eaf765f01b', 'a32b1c81-b500-4842-8e2c-13c1e5d28535', '52e2fdf7-6596-43ed-b71c-be55ae5c91a2', '5688e973-c351-4a6d-ac24-04f23e8eca5e', 'b5cc3e8f-0c01-4b6e-9a23-845ae61f6833', 'c4ec30f4-f61e-49ab-b4be-4e1a9a20d198', '0aab9089-ba41-4a44-a44b-1c3b441c4983', 'd5555df9-09b8-45d4-8438-71051990778f', '0b6132d2-7f30-4cbd-b28d-1180fe0b6dcc', '6395a47e-a54a-440b-b28e-9a5d67172fed', '71ffe39e-e513-48c8-a6ca-f30d5fd8f1da', 'b28472b5-9126-4928-9ca5-27824807621c', '3a8fe1c9-cedd-47ec-9506-7b00b96f1110', '0d0d362b-b71f-42d1-a48a-0dcd8a01d13a', '5e365bff-cac4-4e4a-9592-2f9564ae6a11', '606546b6-4d10-4883-bfa3-cb0e3d6ff4c8', '22c85a01-d2f2-41ec-80fc-8f2e824c1d7a', '1bc5b106-63ab-4f8e-9b16-78cc37485ccc', '9425234f-b0b6-49ef-8d57-0ec12ce2e

In [62]:
ynab.transactions.get_transactions_from_account(budget_id=ynab_budget_id, account_id=ynab_account_id).data.transactions[-1].id

'c56a0322-4527-4eab-8b41-4ab9e3fec2af'

What should be done next:
* See if you can make it so that 'deleted' YNAB transactions that are actually manually deleted, don't show up
    * so: if something is ['deleted'] == 'true', don't send it to YNAB
* and then the other side: from YNAB to Splitwise